In [ ]:
import pandas as pd
import numpy as np

In [ ]:
ds = '/content/drive/MyDrive/Colab Notebooks/Crime_Data_from_2020_to_Present.csv'
pd.options.display.max_columns = None
d = pd.read_csv(ds)
d.head(2)

<ipython-input-2-138e677bb088>:3: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  d = pd.read_csv(ds)


DR_NO               Date Rptd                DATE OCC  TIME OCC  AREA  \
0  190326475  03/01/2020 12:00:00 AM  03/01/2020 12:00:00 AM    2130.0   7.0   
1  200106753  02/09/2020 12:00:00 AM  02/08/2020 12:00:00 AM    1800.0   1.0   

  AREA NAME  Rpt Dist No  Part 1-2  Crm Cd            Crm Cd Desc  \
0  Wilshire        784.0       1.0   510.0       VEHICLE - STOLEN   
1   Central        182.0       1.0   330.0  BURGLARY FROM VEHICLE   

          Mocodes  Vict Age Vict Sex Vict Descent  Premis Cd  \
0             NaN       0.0        M            O      101.0   
1  1822 1402 0344      47.0        M            O      128.0   

                         Premis Desc  Weapon Used Cd Weapon Desc Status  \
0                             STREET             NaN         NaN     AA   
1  BUS STOP/LAYOVER (ALSO QUERY 124)             NaN         NaN     IC   

    Status Desc  Crm Cd 1  Crm Cd 2  Crm Cd 3  Crm Cd 4  \
0  Adult Arrest     510.0     998.0       NaN       NaN   
1   Invest Cont     330.0     998.0       NaN       NaN   

                                  LOCATION Cross Street      LAT       LON  
0  1900 S  LONGWOOD                     AV          NaN  34.0375 -118.3506  
1  1000 S  FLOWER                       ST          NaN  34.0444 -118.2628

deleting rows more than 70% Nan

In [ ]:
threshold_pct = 0.7
missing_counts = d.isna().sum(axis=1)
d = d[missing_counts / len(d.columns) < threshold_pct]

Time of occurence

In [ ]:
def f(x):
    if (x > 4) and (x <= 8) or (x > 400) and (x <= 800):
        return 'Early Morning'
    elif (x > 8) and (x <= 12 ) or (x > 800) and (x <= 1200 ):
        return 'Morning'
    elif (x > 12) and (x <= 16) or (x > 1200) and (x <= 1600):
        return'Afternoon'
    elif (x > 16) and (x <= 20) or (x > 1600) and (x <= 2000):
        return 'Evening'
    elif (x > 20) and (x <= 24) or (x > 2000) and (x <= 2400):
        return'Night'
    elif (x <= 4) or (x <= 400):
        return'Late Night'

d['hour'] = d['TIME OCC'].apply(f)

In [ ]:
d[['TIME OCC', 'hour']].head(2)

TIME OCC     hour
0    2130.0    Night
1    1800.0  Evening

Cleaning location column

In [ ]:

def clean_location(location_string):

  parts = location_string.split(' ')


  parts = [part for part in parts if part]


  street_number = parts[0]


  direction = parts[1] if len(parts) > 1 else None


  street_name = ' '.join(parts[2:])


  cleaned_location = f"{street_number} {' '.join([direction, street_name]) if direction else street_name}"

  return cleaned_location


d['LOCATION'] = d['LOCATION'].apply(clean_location)


#d.head()


Merging Area location etc

In [ ]:
d['AREA_LOCATION'] = d.apply(lambda row: ' '.join([str(row['AREA']), str(row['AREA NAME']), str(row['LOCATION'])]), axis=1)

Keeping only male and female victims

In [ ]:
d = d[d['Vict Sex'].isin(['M', 'F'])]

Replaceing missing values

In [ ]:
d['Premis Cd'] = d['Premis Cd'].fillna(0)

<ipython-input-9-afe0a50ace8f>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  d['Premis Cd'] = d['Premis Cd'].fillna(0)


Taking a sample

In [ ]:
sample_d_1 = d.sample(10000)
sample_d_1.head(2)

DR_NO               Date Rptd                DATE OCC  TIME OCC  \
197148  200612289  07/07/2020 12:00:00 AM  07/06/2020 12:00:00 AM    1900.0   
396145  210110774  05/24/2021 12:00:00 AM  05/05/2021 12:00:00 AM    1220.0   

        AREA  AREA NAME  Rpt Dist No  Part 1-2  Crm Cd  \
197148   6.0  Hollywood        649.0       1.0   350.0   
396145   1.0    Central        145.0       1.0   341.0   

                                              Crm Cd Desc  \
197148                                      THEFT, PERSON   
396145  THEFT-GRAND ($950.01 & OVER)EXCPT,GUNS,FOWL,LI...   

                    Mocodes  Vict Age Vict Sex Vict Descent  Premis Cd  \
197148       0305 0344 1822      45.0        M            O      101.0   
396145  1820 0421 0913 0344      50.0        M            W      502.0   

                                         Premis Desc  Weapon Used Cd  \
197148                                        STREET             NaN   
396145  MULTI-UNIT DWELLING (APARTMENT, DUPLEX, ETC)             NaN   

       Weapon Desc Status  Status Desc  Crm Cd 1  Crm Cd 2  Crm Cd 3  \
197148         NaN     IC  Invest Cont     350.0       NaN       NaN   
396145         NaN     IC  Invest Cont     341.0       NaN       NaN   

        Crm Cd 4             LOCATION Cross Street      LAT       LON  \
197148       NaN  5100 W HOLLYWOOD BL          NaN  34.1018 -118.3009   
396145       NaN         100 E 5TH ST          NaN  34.0471 -118.2474   

             hour                      AREA_LOCATION  
197148    Evening  6.0 Hollywood 5100 W HOLLYWOOD BL  
396145  Afternoon           1.0 Central 100 E 5TH ST

Dropping columns

In [ ]:
imp_sample_d_1 = sample_d_1.drop(['DR_NO', 'Date Rptd','DATE OCC', 'TIME OCC','AREA','Rpt Dist No', 'Part 1-2','Crm Cd Desc',
                                  'Vict Age','Vict Descent', 'Premis Desc', 'Weapon Desc','Weapon Used Cd', 'Status', 'Status Desc', 'Crm Cd 1',
                                  'Crm Cd 2', 'Crm Cd 3', 'Crm Cd 4','LOCATION','Cross Street','AREA NAME', 'LAT','LON', 'Mocodes' ],axis = 1)


In [ ]:
imp_sample_d_1.head(2)

Crm Cd Vict Sex  Premis Cd       hour  \
197148   350.0        M      101.0    Evening   
396145   341.0        M      502.0  Afternoon   

                            AREA_LOCATION  
197148  6.0 Hollywood 5100 W HOLLYWOOD BL  
396145           1.0 Central 100 E 5TH ST

Gender Encoding

In [ ]:
#one hot encoding


victim_encoded_df = pd.get_dummies(imp_sample_d_1, columns = ['Vict Sex'], dtype = 'int')

victim_encoded_df = victim_encoded_df.drop(['Crm Cd','Premis Cd','hour','AREA_LOCATION'], axis=1)

victim_encoded_df.head(2)

Vict Sex_F  Vict Sex_M
197148           0           1
396145           0           1

Hour encoding

In [ ]:
#one hot encoding

hour_encoded_df = pd.get_dummies(imp_sample_d_1, columns = ['hour'], dtype = 'int')

hour_encoded_df = hour_encoded_df.drop(['Crm Cd','Premis Cd','Vict Sex','AREA_LOCATION'], axis=1)

hour_encoded_df.head(2)

hour_Afternoon  hour_Early Morning  hour_Evening  hour_Late Night  \
197148               0                   0             1                0   
396145               1                   0             0                0   

        hour_Morning  hour_Night  
197148             0           0  
396145             0           0

Area Location encoding

In [ ]:
place_encoded_df = pd.get_dummies(imp_sample_d_1, columns = ['AREA_LOCATION'], dtype = 'int')

place_encoded_df = place_encoded_df.drop(['Crm Cd','Premis Cd','Vict Sex','hour'], axis=1)

place_encoded_df.head(2)

AREA_LOCATION_1.0 Central 00 GATEWAY PLZ  \
197148                                         0   
396145                                         0   

        AREA_LOCATION_1.0 Central 100 E 3RD ST  \
197148                                       0   
396145                                       0   

        AREA_LOCATION_1.0 Central 100 E 5TH ST  \
197148                                       0   
396145                                       1   

        AREA_LOCATION_1.0 Central 100 ELLISON ONIZUKA ST  \
197148                                                 0   
396145                                                 0   

        AREA_LOCATION_1.0 Central 100 JAPANESE VILLAGE PLAZA ML  \
197148                                                  0         
396145                                                  0         

        AREA_LOCATION_1.0 Central 100 JUDGE JOHN AISO ST  \
197148                                                 0   
396145                                                 0   

        AREA_LOCATION_1.0 Central 100 N CENTRAL AV  \
197148                                           0   
396145                                           0   

        AREA_LOCATION_1.0 Central 100 N FIGUEROA ST  \
197148                                            0   
396145                                            0   

        AREA_LOCATION_1.0 Central 100 N GRAND AV  \
197148                                         0   
396145                                         0   

        AREA_LOCATION_1.0 Central 100 N HILL ST  \
197148                                        0   
396145                                        0   

        AREA_LOCATION_1.0 Central 100 N JUDGE JOHN AISO ST  \
197148                                                  0    
396145                                                  0    

        AREA_LOCATION_1.0 Central 100 PASEO DE LA PLAZA  \
197148                                                0   
396145                                                0   

        AREA_LOCATION_1.0 Central 100 S FIGUEROA ST  \
197148                                            0   
396145                                            0   

        AREA_LOCATION_1.0 Central 100 S HILL ST  \
197148                                        0   
396145                                        0   

        AREA_LOCATION_1.0 Central 100 S LOS ANGELES ST  \
197148                                               0   
396145                                               0   

        AREA_LOCATION_1.0 Central 100 S VIGNES ST  \
197148                                          0   
396145                                          0   

        AREA_LOCATION_1.0 Central 100 W 1ST ST  \
197148                                       0   
396145                                       0   

        AREA_LOCATION_1.0 Central 100 W 5TH ST  \
197148                                       0   
396145                                       0   

        AREA_LOCATION_1.0 Central 100 W 6TH ST  \
197148                                       0   
396145                                       0   

        AREA_LOCATION_1.0 Central 100 W 7TH ST  \
197148                                       0   
396145                                       0   

        AREA_LOCATION_1.0 Central 100 W ELMYRA ST  \
197148                                          0   
396145                                          0   

        AREA_LOCATION_1.0 Central 1000 FIGUEROA TR  \
197148                                           0   
396145                                           0   

        AREA_LOCATION_1.0 Central 1000 S BROADWAY  \
197148                                          0   
396145                                          0   

        AREA_LOCATION_1.0 Central 1000 S FIGUEROA ST  \
197148                                             0   
396145                                             0   

        AREA_LOCATION_1.0 Central 1000 S FLOWER ST  \
197148         

Keeping only Crime and Premis in main df since others are encoded

In [ ]:
imp_sample_d_1 = imp_sample_d_1.drop(['Vict Sex','hour','AREA_LOCATION'], axis=1)

In [ ]:
imp_sample_d_1.head(2)

Crm Cd  Premis Cd
197148   350.0      101.0
396145   341.0      502.0

Combining all the encoded dataframes together in a df

In [ ]:
categorical_df = pd.concat([victim_encoded_df,hour_encoded_df,place_encoded_df],axis=1)

Combining the encoded categorical df with main df(codes)

In [ ]:
combined_df = pd.concat([categorical_df, imp_sample_d_1], axis=1)

In [ ]:
combined_df.head(1)

Vict Sex_F  Vict Sex_M  hour_Afternoon  hour_Early Morning  \
197148           0           1               0                   0   

        hour_Evening  hour_Late Night  hour_Morning  hour_Night  \
197148             1                0             0           0   

        AREA_LOCATION_1.0 Central 00 GATEWAY PLZ  \
197148                                         0   

        AREA_LOCATION_1.0 Central 100 E 3RD ST  \
197148                                       0   

        AREA_LOCATION_1.0 Central 100 E 5TH ST  \
197148                                       0   

        AREA_LOCATION_1.0 Central 100 ELLISON ONIZUKA ST  \
197148                                                 0   

        AREA_LOCATION_1.0 Central 100 JAPANESE VILLAGE PLAZA ML  \
197148                                                  0         

        AREA_LOCATION_1.0 Central 100 JUDGE JOHN AISO ST  \
197148                                                 0   

        AREA_LOCATION_1.0 Central 100 N CENTRAL AV  \
197148                                           0   

        AREA_LOCATION_1.0 Central 100 N FIGUEROA ST  \
197148                                            0   

        AREA_LOCATION_1.0 Central 100 N GRAND AV  \
197148                                         0   

        AREA_LOCATION_1.0 Central 100 N HILL ST  \
197148                                        0   

        AREA_LOCATION_1.0 Central 100 N JUDGE JOHN AISO ST  \
197148                                                  0    

        AREA_LOCATION_1.0 Central 100 PASEO DE LA PLAZA  \
197148                                                0   

        AREA_LOCATION_1.0 Central 100 S FIGUEROA ST  \
197148                                            0   

        AREA_LOCATION_1.0 Central 100 S HILL ST  \
197148                                        0   

        AREA_LOCATION_1.0 Central 100 S LOS ANGELES ST  \
197148                                               0   

        AREA_LOCATION_1.0 Central 100 S VIGNES ST  \
197148                                          0   

        AREA_LOCATION_1.0 Central 100 W 1ST ST  \
197148                                       0   

        AREA_LOCATION_1.0 Central 100 W 5TH ST  \
197148                                       0   

        AREA_LOCATION_1.0 Central 100 W 6TH ST  \
197148                                       0   

        AREA_LOCATION_1.0 Central 100 W 7TH ST  \
197148                                       0   

        AREA_LOCATION_1.0 Central 100 W ELMYRA ST  \
197148                                          0   

        AREA_LOCATION_1.0 Central 1000 FIGUEROA TR  \
197148                                           0   

        AREA_LOCATION_1.0 Central 1000 S BROADWAY  \
197148                                          0   

        AREA_LOCATION_1.0 Central 1000 S FIGUEROA ST  \
197148                                             0   

        AREA_LOCATION_1.0 Central 1000 S FLOWER ST  \
197148                                           0   

        AREA_LOCATION_1.0 Central 1000 S GRAND AV  \
197148                                          0   

        AREA_LOCATION_1.0 Central 1000 S HILL ST  \
197148                                         0   

        AREA_LOCATION_1.0 Central 1000 S HOPE ST  \
197148                                         0   

        AREA_LOCATION_1.0 Central 1000 S LOS ANGELES ST  \
197148                                                0   

        AREA_LOCATION_1.0 Central 1000 S OLIVE ST  \
197148                                          0   

        AREA_LOCATION_1.0 Central 1000 WILSHIRE BL  \
197148                                           0   

        AREA_LOCATION_1.0 Central 1100 MAPLE AV  \
197148                                        0   

        AREA_LOCATION_1.0 Central 1100 S FIGUEROA ST  \
197148                                             0   

        AREA_LOCATION_1.0 Central 1100 S GRAND AV  \
197148                                          0   

        AREA_L

ORDER 5

New Table for Results

In [ ]:
SilhouetteTable5 = pd.DataFrame()
DaviesBouldinTable5 = pd.DataFrame()

Dropping columns

In [ ]:
imp_sample_d_1 = sample_d_1.drop(['DR_NO', 'Date Rptd','DATE OCC', 'TIME OCC','AREA','Rpt Dist No', 'Part 1-2','Crm Cd Desc',
                                  'Vict Age','Vict Descent', 'Premis Desc', 'Weapon Desc','Weapon Used Cd', 'Status', 'Status Desc', 'Crm Cd 1',
                                  'Crm Cd 2', 'Crm Cd 3', 'Crm Cd 4','LOCATION','Cross Street','AREA NAME', 'LAT','LON', 'Mocodes' ],axis = 1)


Keeping only Crime and Premis in main df since others are encoded

In [ ]:
imp_sample_d_1 = imp_sample_d_1.drop(['Vict Sex','hour','AREA_LOCATION'], axis=1)

KMEANS

1. Gender Area

In [ ]:
ga = pd.concat([victim_encoded_df,place_encoded_df ],axis = 1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb51 = sc.fit_transform(ga)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb51)

principalDf51 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from matplotlib.pyplot import plot
from sklearn.cluster import KMeans

k=10
kmeans = KMeans(n_clusters=4)
kmeans.fit(principalDf51)
clusters = kmeans.labels_
centroids = kmeans.cluster_centers_

imp_sample_d_1['cluster1_k'] = kmeans.labels_

/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)


2. Gender Area Premise

In [ ]:
imp_sample_d_11 = imp_sample_d_1.drop(['Crm Cd'],axis = 1)
#imp_sample_d_11.head(1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb52 = sc.fit_transform(imp_sample_d_11)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb52)

principalDf52 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from matplotlib.pyplot import plot
from sklearn.cluster import KMeans

k=10
kmeans = KMeans(n_clusters=4)
kmeans.fit(principalDf52)
clusters = kmeans.labels_
centroids = kmeans.cluster_centers_

imp_sample_d_1['cluster2_k'] = kmeans.labels_

/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)


3. Gender Area Premise Hour


In [ ]:
imp_sample_d_12 = imp_sample_d_1.drop(['Crm Cd','Premis Cd','cluster1_k'],axis = 1)
#imp_sample_d_12.head(1)

In [ ]:
gaph = pd.concat([hour_encoded_df, imp_sample_d_12],axis = 1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb53 = sc.fit_transform(gaph)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb53)

principalDf53 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from matplotlib.pyplot import plot
from sklearn.cluster import KMeans

k=10
kmeans = KMeans(n_clusters=4)
kmeans.fit(principalDf53)
clusters = kmeans.labels_
centroids = kmeans.cluster_centers_

imp_sample_d_1['cluster3_k'] = kmeans.labels_

/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)


4. Gender Area Premise Hour Crime

In [ ]:
imp_sample_d_13 = imp_sample_d_1.drop(['cluster2_k','Premis Cd','cluster1_k'],axis = 1)
imp_sample_d_13.head(1)

Crm Cd  cluster3_k
197148   350.0           2

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb54 = sc.fit_transform(imp_sample_d_13)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb54)

principalDf54 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from matplotlib.pyplot import plot
from sklearn.cluster import KMeans

k=10
kmeans = KMeans(n_clusters=4)
kmeans.fit(principalDf54)
clusters = kmeans.labels_
centroids = kmeans.cluster_centers_

imp_sample_d_1['cluster4_k'] = kmeans.labels_

/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)


Silhouette Score

In [ ]:
from sklearn.metrics import silhouette_score

SilhouetteTable5['KMEAN'] =  [silhouette_score(principalDf54,imp_sample_d_1['cluster4_k'] )]

Davies Bouldin Score

In [ ]:
from sklearn.metrics import davies_bouldin_score
DaviesBouldinTable5['KMEAN'] =  [davies_bouldin_score(principalDf54, imp_sample_d_1['cluster4_k'])]

DBSCAN

Dropping columns

In [ ]:
imp_sample_d_1 = sample_d_1.drop(['DR_NO', 'Date Rptd','DATE OCC', 'TIME OCC','AREA','Rpt Dist No', 'Part 1-2','Crm Cd Desc',
                                  'Vict Age','Vict Descent', 'Premis Desc', 'Weapon Desc','Weapon Used Cd', 'Status', 'Status Desc', 'Crm Cd 1',
                                  'Crm Cd 2', 'Crm Cd 3', 'Crm Cd 4','LOCATION','Cross Street','AREA NAME', 'LAT','LON', 'Mocodes' ],axis = 1)


Keeping only Crime and Premis in main df since others are encoded

In [ ]:
imp_sample_d_1 = imp_sample_d_1.drop(['Vict Sex','hour','AREA_LOCATION'], axis=1)

1. Gender Area

In [ ]:
ga = pd.concat([victim_encoded_df,place_encoded_df ],axis = 1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb51 = sc.fit_transform(ga)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb51)

principalDf51 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.cluster import DBSCAN

db = DBSCAN(eps=0.1, min_samples=4).fit(principalDf51)
labels = db.labels_

n_clusters_ = len(set(labels)) - (1 if -1 in labels else 0)
n_noise_ = list(labels).count(-1)

# print('Estimated number of clusters: %d' % n_clusters_)
# print('Estimated number of noise points: %d' % n_noise_)

imp_sample_d_1['cluster1_d']= labels

2. Gender Area Premise

In [ ]:
imp_sample_d_11 = imp_sample_d_1.drop(['Crm Cd'],axis = 1)
#imp_sample_d_11.head(1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb52 = sc.fit_transform(imp_sample_d_11)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb52)

principalDf52 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.cluster import DBSCAN

db = DBSCAN(eps=0.1, min_samples=4).fit(principalDf52)
labels = db.labels_

n_clusters_ = len(set(labels)) - (1 if -1 in labels else 0)
n_noise_ = list(labels).count(-1)

# print('Estimated number of clusters: %d' % n_clusters_)
# print('Estimated number of noise points: %d' % n_noise_)

imp_sample_d_1['cluster2_d']= labels

3. Gender Area Premise Hour


In [ ]:
imp_sample_d_12 = imp_sample_d_1.drop(['Crm Cd','Premis Cd','cluster1_d'],axis = 1)
#imp_sample_d_12.head(1)

In [ ]:
gaph = pd.concat([hour_encoded_df, imp_sample_d_12],axis = 1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb53 = sc.fit_transform(gaph)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb53)

principalDf53 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.cluster import DBSCAN

db = DBSCAN(eps=0.1, min_samples=4).fit(principalDf53)
labels = db.labels_

n_clusters_ = len(set(labels)) - (1 if -1 in labels else 0)
n_noise_ = list(labels).count(-1)

# print('Estimated number of clusters: %d' % n_clusters_)
# print('Estimated number of noise points: %d' % n_noise_)

imp_sample_d_1['cluster3_d']= labels

4. Gender Area Premise Hour Crime

In [ ]:
imp_sample_d_13 = imp_sample_d_1.drop(['cluster2_d','Premis Cd','cluster1_d'],axis = 1)
imp_sample_d_13.head(1)

Crm Cd  cluster3_d
197148   350.0           0

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb54 = sc.fit_transform(imp_sample_d_13)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb54)

principalDf54 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.cluster import DBSCAN

db = DBSCAN(eps=0.1, min_samples=4).fit(principalDf54)
labels = db.labels_

n_clusters_ = len(set(labels)) - (1 if -1 in labels else 0)
n_noise_ = list(labels).count(-1)

# print('Estimated number of clusters: %d' % n_clusters_)
# print('Estimated number of noise points: %d' % n_noise_)

imp_sample_d_1['cluster4_d']= labels

Silhouette Score

In [ ]:
from sklearn.metrics import silhouette_score

SilhouetteTable5['DBSCAN'] =  [silhouette_score(principalDf54,imp_sample_d_1['cluster4_d'] )]

Davies Bouldin Score

In [ ]:
from sklearn.metrics import davies_bouldin_score
DaviesBouldinTable5['DBSCAN'] =  [davies_bouldin_score(principalDf54, imp_sample_d_1['cluster4_d'])]

HIERARCHICAL AGGLOMERATIVE

Dropping columns

In [ ]:
imp_sample_d_1 = sample_d_1.drop(['DR_NO', 'Date Rptd','DATE OCC', 'TIME OCC','AREA','Rpt Dist No', 'Part 1-2','Crm Cd Desc',
                                  'Vict Age','Vict Descent', 'Premis Desc', 'Weapon Desc','Weapon Used Cd', 'Status', 'Status Desc', 'Crm Cd 1',
                                  'Crm Cd 2', 'Crm Cd 3', 'Crm Cd 4','LOCATION','Cross Street','AREA NAME', 'LAT','LON', 'Mocodes' ],axis = 1)


Keeping only Crime and Premis in main df since others are encoded

In [ ]:
imp_sample_d_1 = imp_sample_d_1.drop(['Vict Sex','hour','AREA_LOCATION'], axis=1)

1. Gender Area

In [ ]:
ga = pd.concat([victim_encoded_df,place_encoded_df ],axis = 1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb51 = sc.fit_transform(ga)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb51)

principalDf51 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
import pandas as pd
from sklearn.cluster import AgglomerativeClustering

model = AgglomerativeClustering(n_clusters=4, linkage='average')

model.fit(principalDf51)

imp_sample_d_1['cluster1_h'] = model.labels_

2. Gender Area Premise

In [ ]:
imp_sample_d_11 = imp_sample_d_1.drop(['Crm Cd'],axis = 1)
#imp_sample_d_11.head(1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb52 = sc.fit_transform(imp_sample_d_11)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb52)

principalDf52 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
import pandas as pd
from sklearn.cluster import AgglomerativeClustering

model = AgglomerativeClustering(n_clusters=4, linkage='average')

model.fit(principalDf52)

imp_sample_d_1['cluster2_h'] = model.labels_

3. Gender Area Premise Hour


In [ ]:
imp_sample_d_12 = imp_sample_d_1.drop(['Crm Cd','Premis Cd','cluster1_h'],axis = 1)
#imp_sample_d_12.head(1)

In [ ]:
gaph = pd.concat([hour_encoded_df, imp_sample_d_12],axis = 1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb53 = sc.fit_transform(gaph)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb53)

principalDf53 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
import pandas as pd
from sklearn.cluster import AgglomerativeClustering

model = AgglomerativeClustering(n_clusters=4, linkage='average')

model.fit(principalDf53)

imp_sample_d_1['cluster3_h'] = model.labels_

4. Gender Area Premise Hour Crime

In [ ]:
imp_sample_d_13 = imp_sample_d_1.drop(['cluster2_h','Premis Cd','cluster1_h'],axis = 1)
imp_sample_d_13.head(1)

Crm Cd  cluster3_h
197148   350.0           2

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb54 = sc.fit_transform(imp_sample_d_13)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb54)

principalDf54 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
import pandas as pd
from sklearn.cluster import AgglomerativeClustering

model = AgglomerativeClustering(n_clusters=4, linkage='average')

model.fit(principalDf54)

imp_sample_d_1['cluster4_h'] = model.labels_

Silhouette Score

In [ ]:
from sklearn.metrics import silhouette_score

SilhouetteTable5['HIERARCHICAL_AGGLO_AVE'] =  [silhouette_score(principalDf54,imp_sample_d_1['cluster4_h'] )]

Davies Bouldin Score

In [ ]:
from sklearn.metrics import davies_bouldin_score
DaviesBouldinTable5['HIERARCHICAL_AGGLO_AVE'] =  [davies_bouldin_score(principalDf54, imp_sample_d_1['cluster4_h'])]

HDBSCAN

Dropping columns

In [ ]:
imp_sample_d_1 = sample_d_1.drop(['DR_NO', 'Date Rptd','DATE OCC', 'TIME OCC','AREA','Rpt Dist No', 'Part 1-2','Crm Cd Desc',
                                  'Vict Age','Vict Descent', 'Premis Desc', 'Weapon Desc','Weapon Used Cd', 'Status', 'Status Desc', 'Crm Cd 1',
                                  'Crm Cd 2', 'Crm Cd 3', 'Crm Cd 4','LOCATION','Cross Street','AREA NAME', 'LAT','LON', 'Mocodes' ],axis = 1)


Keeping only Crime and Premis in main df since others are encoded

In [ ]:
imp_sample_d_1 = imp_sample_d_1.drop(['Vict Sex','hour','AREA_LOCATION'], axis=1)

1. Gender Area

In [ ]:
ga = pd.concat([victim_encoded_df,place_encoded_df ],axis = 1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb51 = sc.fit_transform(ga)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb51)

principalDf51 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
pip install hdbscan

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.6/3.6 MB 54.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.9/1.9 MB 50.6 MB/s eta 0:00:00
  Attempting uninstall: cython
    Found existing installation: Cython 3.0.10
    Uninstalling Cython-3.0.10:
      Successfully uninstalled Cython-3.0.10


In [ ]:
import hdbscan

clusterer = hdbscan.HDBSCAN()

cluster_labels = clusterer.fit_predict(principalDf51)

imp_sample_d_1['cluster1_hdb'] = cluster_labels

2. Gender Area Premise

In [ ]:
imp_sample_d_11 = imp_sample_d_1.drop(['Crm Cd'],axis = 1)
#imp_sample_d_11.head(1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb52 = sc.fit_transform(imp_sample_d_11)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb52)

principalDf52 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
import hdbscan

clusterer = hdbscan.HDBSCAN()

cluster_labels = clusterer.fit_predict(principalDf52)

imp_sample_d_1['cluster2_hdb'] = cluster_labels

3. Gender Area Premise Hour


In [ ]:
imp_sample_d_12 = imp_sample_d_1.drop(['Crm Cd','Premis Cd','cluster1_hdb'],axis = 1)
#imp_sample_d_12.head(1)

In [ ]:
gaph = pd.concat([hour_encoded_df, imp_sample_d_12],axis = 1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb53 = sc.fit_transform(gaph)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb53)

principalDf53 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
import hdbscan

clusterer = hdbscan.HDBSCAN()

cluster_labels = clusterer.fit_predict(principalDf53)

imp_sample_d_1['cluster3_hdb'] = cluster_labels

4. Gender Area Premise Hour Crime

In [ ]:
imp_sample_d_13 = imp_sample_d_1.drop(['cluster2_hdb','Premis Cd','cluster1_hdb'],axis = 1)
imp_sample_d_13.head(1)

Crm Cd  cluster3_hdb
197148   350.0           195

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb54 = sc.fit_transform(imp_sample_d_13)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb54)

principalDf54 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
import hdbscan

clusterer = hdbscan.HDBSCAN()

cluster_labels = clusterer.fit_predict(principalDf54)

imp_sample_d_1['cluster4_hdb'] = cluster_labels

Silhouette Score

In [ ]:
from sklearn.metrics import silhouette_score

SilhouetteTable5['HDBSCAN'] =  [silhouette_score(principalDf54,imp_sample_d_1['cluster4_hdb'] )]

Davies Bouldin Score

In [ ]:
from sklearn.metrics import davies_bouldin_score
DaviesBouldinTable5['HDBSCAN'] =  [davies_bouldin_score(principalDf54, imp_sample_d_1['cluster4_hdb'])]

OPTICS

Dropping columns

In [ ]:
imp_sample_d_1 = sample_d_1.drop(['DR_NO', 'Date Rptd','DATE OCC', 'TIME OCC','AREA','Rpt Dist No', 'Part 1-2','Crm Cd Desc',
                                  'Vict Age','Vict Descent', 'Premis Desc', 'Weapon Desc','Weapon Used Cd', 'Status', 'Status Desc', 'Crm Cd 1',
                                  'Crm Cd 2', 'Crm Cd 3', 'Crm Cd 4','LOCATION','Cross Street','AREA NAME', 'LAT','LON', 'Mocodes' ],axis = 1)


Keeping only Crime and Premis in main df since others are encoded

In [ ]:
imp_sample_d_1 = imp_sample_d_1.drop(['Vict Sex','hour','AREA_LOCATION'], axis=1)

1. Gender Area

In [ ]:
ga = pd.concat([victim_encoded_df,place_encoded_df ],axis = 1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb51 = sc.fit_transform(ga)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb51)

principalDf51 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.cluster import OPTICS

clustering = OPTICS()

labels = clustering.fit_predict(principalDf51)

imp_sample_d_1['cluster1_o'] = labels

/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_optics.py:995: RuntimeWarning: divide by zero encountered in divide
  ratio = reachability_plot[:-1] / reachability_plot[1:]


2. Gender Area Premise

In [ ]:
imp_sample_d_11 = imp_sample_d_1.drop(['Crm Cd'],axis = 1)
#imp_sample_d_11.head(1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb52 = sc.fit_transform(imp_sample_d_11)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb52)

principalDf52 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.cluster import OPTICS

clustering = OPTICS()

labels = clustering.fit_predict(principalDf52)

imp_sample_d_1['cluster2_o'] = labels

/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_optics.py:995: RuntimeWarning: divide by zero encountered in divide
  ratio = reachability_plot[:-1] / reachability_plot[1:]


3. Gender Area Premise Hour


In [ ]:
imp_sample_d_12 = imp_sample_d_1.drop(['Crm Cd','Premis Cd','cluster1_o'],axis = 1)
#imp_sample_d_12.head(1)

In [ ]:
gaph = pd.concat([hour_encoded_df, imp_sample_d_12],axis = 1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb53 = sc.fit_transform(gaph)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb53)

principalDf53 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.cluster import OPTICS

clustering = OPTICS()

labels = clustering.fit_predict(principalDf53)

imp_sample_d_1['cluster3_o'] = labels

/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_optics.py:995: RuntimeWarning: divide by zero encountered in divide
  ratio = reachability_plot[:-1] / reachability_plot[1:]


4. Gender Area Premise Hour Crime

In [ ]:
imp_sample_d_13 = imp_sample_d_1.drop(['cluster2_o','Premis Cd','cluster1_o'],axis = 1)
imp_sample_d_13.head(1)

Crm Cd  cluster3_o
197148   350.0           0

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb54 = sc.fit_transform(imp_sample_d_13)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb54)

principalDf54 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.cluster import OPTICS

clustering = OPTICS()

labels = clustering.fit_predict(principalDf54)

imp_sample_d_1['cluster4_o'] = labels

/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_optics.py:995: RuntimeWarning: divide by zero encountered in divide
  ratio = reachability_plot[:-1] / reachability_plot[1:]


Silhouette Score

In [ ]:
from sklearn.metrics import silhouette_score

SilhouetteTable5['OPTICS'] =  [silhouette_score(principalDf54,imp_sample_d_1['cluster4_o'] )]

Davies Bouldin Score

In [ ]:
from sklearn.metrics import davies_bouldin_score
DaviesBouldinTable5['OPTICS'] =  [davies_bouldin_score(principalDf54, imp_sample_d_1['cluster4_o'])]

BIRCH

Dropping columns

In [ ]:
imp_sample_d_1 = sample_d_1.drop(['DR_NO', 'Date Rptd','DATE OCC', 'TIME OCC','AREA','Rpt Dist No', 'Part 1-2','Crm Cd Desc',
                                  'Vict Age','Vict Descent', 'Premis Desc', 'Weapon Desc','Weapon Used Cd', 'Status', 'Status Desc', 'Crm Cd 1',
                                  'Crm Cd 2', 'Crm Cd 3', 'Crm Cd 4','LOCATION','Cross Street','AREA NAME', 'LAT','LON', 'Mocodes' ],axis = 1)


Keeping only Crime and Premis in main df since others are encoded

In [ ]:
imp_sample_d_1 = imp_sample_d_1.drop(['Vict Sex','hour','AREA_LOCATION'], axis=1)

1. Gender Area

In [ ]:
ga = pd.concat([victim_encoded_df,place_encoded_df ],axis = 1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb51 = sc.fit_transform(ga)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb51)

principalDf51 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.cluster import Birch

birch = Birch(n_clusters=4)

cluster_b = birch.fit_predict(principalDf51)

imp_sample_d_1['cluster1_b'] = cluster_b

2. Gender Area Premise

In [ ]:
imp_sample_d_11 = imp_sample_d_1.drop(['Crm Cd'],axis = 1)
#imp_sample_d_11.head(1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb52 = sc.fit_transform(imp_sample_d_11)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb52)

principalDf52 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.cluster import Birch

birch = Birch(n_clusters=4)

cluster_b = birch.fit_predict(principalDf52)

imp_sample_d_1['cluster2_b'] = cluster_b

3. Gender Area Premise Hour


In [ ]:
imp_sample_d_12 = imp_sample_d_1.drop(['Crm Cd','Premis Cd','cluster1_b'],axis = 1)
#imp_sample_d_12.head(1)

In [ ]:
gaph = pd.concat([hour_encoded_df, imp_sample_d_12],axis = 1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb53 = sc.fit_transform(gaph)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb53)

principalDf53 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.cluster import Birch

birch = Birch(n_clusters=4)

cluster_b = birch.fit_predict(principalDf53)

imp_sample_d_1['cluster3_b'] = cluster_b

4. Gender Area Premise Hour Crime

In [ ]:
imp_sample_d_13 = imp_sample_d_1.drop(['cluster2_b','Premis Cd','cluster1_b'],axis = 1)
imp_sample_d_13.head(1)

Crm Cd  cluster3_b
197148   350.0           2

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb54 = sc.fit_transform(imp_sample_d_13)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb54)

principalDf54 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.cluster import Birch

birch = Birch(n_clusters=4)

cluster_b = birch.fit_predict(principalDf54)

imp_sample_d_1['cluster4_b'] = cluster_b

Silhouette Score

In [ ]:
from sklearn.metrics import silhouette_score

SilhouetteTable5['BIRCH'] =  [silhouette_score(principalDf54,imp_sample_d_1['cluster4_b'] )]

Davies Bouldin Score

In [ ]:
from sklearn.metrics import davies_bouldin_score
DaviesBouldinTable5['BIRCH'] =  [davies_bouldin_score(principalDf54, imp_sample_d_1['cluster4_b'])]

GMM

Dropping columns

In [ ]:
imp_sample_d_1 = sample_d_1.drop(['DR_NO', 'Date Rptd','DATE OCC', 'TIME OCC','AREA','Rpt Dist No', 'Part 1-2','Crm Cd Desc',
                                  'Vict Age','Vict Descent', 'Premis Desc', 'Weapon Desc','Weapon Used Cd', 'Status', 'Status Desc', 'Crm Cd 1',
                                  'Crm Cd 2', 'Crm Cd 3', 'Crm Cd 4','LOCATION','Cross Street','AREA NAME', 'LAT','LON', 'Mocodes' ],axis = 1)


Keeping only Crime and Premis in main df since others are encoded

In [ ]:
imp_sample_d_1 = imp_sample_d_1.drop(['Vict Sex','hour','AREA_LOCATION'], axis=1)

1. Gender Area

In [ ]:
ga = pd.concat([victim_encoded_df,place_encoded_df ],axis = 1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb51 = sc.fit_transform(ga)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb51)

principalDf51 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.mixture import GaussianMixture

gmm = GaussianMixture(n_components=4, random_state=42)
gmm.fit(principalDf51)

labels = gmm.predict(principalDf51)


imp_sample_d_1['cluster1_g'] = labels

2. Gender Area Premise

In [ ]:
imp_sample_d_11 = imp_sample_d_1.drop(['Crm Cd'],axis = 1)
#imp_sample_d_11.head(1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb52 = sc.fit_transform(imp_sample_d_11)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb52)

principalDf52 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.mixture import GaussianMixture

gmm = GaussianMixture(n_components=4, random_state=42)
gmm.fit(principalDf52)

labels = gmm.predict(principalDf52)


imp_sample_d_1['cluster2_g'] = labels

3. Gender Area Premise Hour


In [ ]:
imp_sample_d_12 = imp_sample_d_1.drop(['Crm Cd','Premis Cd','cluster1_g'],axis = 1)
#imp_sample_d_12.head(1)

In [ ]:
gaph = pd.concat([hour_encoded_df, imp_sample_d_12],axis = 1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb53 = sc.fit_transform(gaph)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb53)

principalDf53 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.mixture import GaussianMixture

gmm = GaussianMixture(n_components=4, random_state=42)
gmm.fit(principalDf53)

labels = gmm.predict(principalDf53)


imp_sample_d_1['cluster3_g'] = labels

4. Gender Area Premise Hour Crime

In [ ]:
imp_sample_d_13 = imp_sample_d_1.drop(['cluster2_g','Premis Cd','cluster1_g'],axis = 1)
imp_sample_d_13.head(1)

Crm Cd  cluster3_g
197148   350.0           0

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb54 = sc.fit_transform(imp_sample_d_13)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb54)

principalDf54 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.mixture import GaussianMixture

gmm = GaussianMixture(n_components=4, random_state=42)
gmm.fit(principalDf54)

labels = gmm.predict(principalDf54)


imp_sample_d_1['cluster4_g'] = labels

Silhouette Score

In [ ]:
from sklearn.metrics import silhouette_score

SilhouetteTable5['GMM'] =  [silhouette_score(principalDf54,imp_sample_d_1['cluster4_g'] )]

Davies Bouldin Score

In [ ]:
from sklearn.metrics import davies_bouldin_score
DaviesBouldinTable5['GMM'] =  [davies_bouldin_score(principalDf54, imp_sample_d_1['cluster4_g'])]

SPECTRAL

Dropping columns

In [ ]:
imp_sample_d_1 = sample_d_1.drop(['DR_NO', 'Date Rptd','DATE OCC', 'TIME OCC','AREA','Rpt Dist No', 'Part 1-2','Crm Cd Desc',
                                  'Vict Age','Vict Descent', 'Premis Desc', 'Weapon Desc','Weapon Used Cd', 'Status', 'Status Desc', 'Crm Cd 1',
                                  'Crm Cd 2', 'Crm Cd 3', 'Crm Cd 4','LOCATION','Cross Street','AREA NAME', 'LAT','LON', 'Mocodes' ],axis = 1)


Keeping only Crime and Premis in main df since others are encoded

In [ ]:
imp_sample_d_1 = imp_sample_d_1.drop(['Vict Sex','hour','AREA_LOCATION'], axis=1)

1. Gender Area

In [ ]:
ga = pd.concat([victim_encoded_df,place_encoded_df ],axis = 1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb51 = sc.fit_transform(ga)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb51)

principalDf51 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.cluster import SpectralClustering

spectral_model_rbf = SpectralClustering(n_clusters = 4, affinity ='rbf')

labels_rbf = spectral_model_rbf.fit_predict(principalDf51)

imp_sample_d_1['cluster1_s'] = labels_rbf

2. Gender Area Premise

In [ ]:
imp_sample_d_11 = imp_sample_d_1.drop(['Crm Cd'],axis = 1)
#imp_sample_d_11.head(1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb52 = sc.fit_transform(imp_sample_d_11)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb52)

principalDf52 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.cluster import SpectralClustering

spectral_model_rbf = SpectralClustering(n_clusters = 4, affinity ='rbf')

labels_rbf = spectral_model_rbf.fit_predict(principalDf52)

imp_sample_d_1['cluster2_s'] = labels_rbf

3. Gender Area Premise Hour


In [ ]:
imp_sample_d_12 = imp_sample_d_1.drop(['Crm Cd','Premis Cd','cluster1_s'],axis = 1)
#imp_sample_d_12.head(1)

In [ ]:
gaph = pd.concat([hour_encoded_df, imp_sample_d_12],axis = 1)

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb53 = sc.fit_transform(gaph)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb53)

principalDf53 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.cluster import SpectralClustering

spectral_model_rbf = SpectralClustering(n_clusters = 4, affinity ='rbf')

labels_rbf = spectral_model_rbf.fit_predict(principalDf53)

imp_sample_d_1['cluster3_s'] = labels_rbf

4. Gender Area Premise Hour Crime

In [ ]:
imp_sample_d_13 = imp_sample_d_1.drop(['cluster2_s','Premis Cd','cluster1_s'],axis = 1)
imp_sample_d_13.head(1)

Crm Cd  cluster3_s
197148   350.0           2

FEATURE SCALING

In [ ]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()

allcomb54 = sc.fit_transform(imp_sample_d_13)

PCA

In [ ]:
from sklearn.decomposition import PCA

pca = PCA(n_components=2)

principalComponents = pca.fit_transform(allcomb54)

principalDf54 = pd.DataFrame(data = principalComponents
             , columns = ['principal component 1', 'principal component 2'])

Algo

In [ ]:
from sklearn.cluster import SpectralClustering

spectral_model_rbf = SpectralClustering(n_clusters = 4, affinity ='rbf')

labels_rbf = spectral_model_rbf.fit_predict(principalDf54)

imp_sample_d_1['cluster4_s'] = labels_rbf

Silhouette Score

In [ ]:
from sklearn.metrics import silhouette_score

SilhouetteTable5['SPECTRAL'] =  [silhouette_score(principalDf54,imp_sample_d_1['cluster4_s'] )]

Davies Bouldin Score

In [ ]:
from sklearn.metrics import davies_bouldin_score
DaviesBouldinTable5['SPECTRAL'] =  [davies_bouldin_score(principalDf54, imp_sample_d_1['cluster4_s'])]

In [ ]:
SilhouetteTable5

KMEAN    DBSCAN  HIERARCHICAL_AGGLO_AVE   HDBSCAN    OPTICS     BIRCH  \
0  0.548655  0.837326                0.502687  0.480254  0.596801  0.445571   

        GMM  SPECTRAL  
0  0.557669  0.495151

In [ ]:
DaviesBouldinTable5

KMEAN    DBSCAN  HIERARCHICAL_AGGLO_AVE   HDBSCAN    OPTICS     BIRCH  \
0  0.66989  0.202283                0.671071  1.222399  1.147891  0.762894   

       GMM  SPECTRAL  
0  0.66193  0.737804

In [ ]:
# print(imp_sample_d_1['Crm Cd'].value_counts().to_string(max_rows=None))